In [1]:
from datasets import load_dataset
import pandas as pd
import os
import re
import string
from tqdm import tqdm

In [2]:
from nltk.tokenize import word_tokenize
import nltk


In [3]:
nltk.data.path.append(os.path.abspath('nltk_data'))

In [4]:

# nltk.download('stopwords' , download_dir='nltk_data')
# nltk.download('wordnet' , download_dir='nltk_data')
nltk.download('punkt_tab', download_dir='nltk_data')

[nltk_data] Downloading package punkt_tab to nltk_data...
[nltk_data]   Package punkt_tab is already up-to-date!


True

---


In [5]:
main_path = os.path.abspath('../../Datasets/CSV/HasilPreprocessingPutusan.csv')

In [6]:
main_df = pd.read_csv(main_path)
main_df

Unnamed: 0                             nama_file  \
0            10  12685851e8dfed8cbd76ae6f4854e65d.txt   
1            12  178fbc570d83459cf7048788fc69d7b7.txt   
2            15  1e056fa0e1ae623af4a86adf45ba39d3.txt   
3            16  236d4c158ce8108d082683f0e2086455.txt   
4            18  2592c509030c63e45c2fbc96647e789d.txt   
..          ...                                   ...   
230         417  zaf016a9bde944e4b157313435313133.txt   
231         418  zaf01fed3c738ab2bf28303934373033.txt   
232         419  zaf0201f53a267a8beb0313534353336.txt   
233         420  zaf0201f55c473d284d9313534353430.txt   
234         421  zaf0240d97731d469c13313534383434.txt   

                Nomor Putusan                     Nama Terdakwa 1  \
0     192/pid. b/2019/pn bkl           h.  abd aziz al.  h.  aziz   
1       9/pid. b/2019/pn bkl         h.  muzammil bin mattingwar.   
2     108/pid. b/2020/pn bkl                              ansori.   
3     294/pid. b/2018/pn. bkl               nama : hatib bin sagi   
4    431 /pid. b/2018/pn bkl,                        moch.  tuki.   
..                        ...                                 ...   
230    31/pid. b/2025/pn bkl    nur holis alias kholis bin selket   
231    47/pid. b/2025/pn bkl   andika dwi tripratama bin suratman   
232    60/pid. b/2020/pn bkl            mat bakri bin jaman (alm)   
233    77/pid. b/2025/pn bkl              muhamad arip bin mahpud   
234    60/pid. b/2025/pn bkl                    sujai bin marikan   

    Nama Terdakwa 2 Nama Terdakwa 3  \
0               NaN             NaN   
1               NaN             NaN   
2           ahmadi.             NaN   
3               NaN             NaN   
4               NaN             NaN   
..              ...             ...   
230             NaN             NaN   
231             NaN             NaN   
232             NaN             NaN   
233             NaN             NaN   
234             NaN             NaN   

                                       Tuntutan Pidana  \
0                         “pencurian dengan kekerasan”   
1                                           “penipuan”   
2    “pencurian yang didahului, disertai atau diiku...   
3                                       "penganiayaan"   
4           penganiayaan yang mengakibatkan luka berat   
..                                                 ...   
230                                      “penggelapan”   
231                             “percobaan pencurian ”   
232                     “pencurian dengan pemberatan ”   
233                    “ pencurian dengan pemberatan ”   
234  “melakukan perbuatan penganiayaan atau dengan ...   

                     Tuntutan KUHP  \
0    pasal 365 ayat (2) ke-1 kitab   
1                   pasal 372 kuhp   
2     pasal 365 ayat (2) ke-2 kuhp   
3          pasal 351 ayat (1) kuhp   
4         pasal 351 ayat ( 2) kuhp   
..                             ...   
230                pasal 372 kitab   
231                 pasal 362 kuhp   
232   pasal 363 ayat (1) ke-4 kuhp   
233   pasal 363 ayat (1) ke-4 kuhp   
234       pasal 351 ayat (1) kitab   

                                      Tuntutan Hukuman  \
0                                       6 (enam) tahun   
1    3 (tiga) penjara dikurangkan seluruhnya selama...   
2    1 (satu) tahun dikurangi selama para terdakwa ...   
3    6(enam) bulan dikurangi selama terdakwa berada...   
4                                       1 (satu) tahun   
..                                                 ...   
230  2 (dua) tahun dikurangi seluruhnya masa penang...   
231                                     1 (satu) tahun   
232                                      2 (dua) tahun   
233                                      2 (dua) tahun   
234                                     1 (satu) tahun   

                                        Putusan Pidana  \
0                        “pencurian dengan kekerasan ”   
1                                     :“ penggelapan “ 

In [7]:
main_df.info()

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 235 entries, 0 to 234
Data columns (total 18 columns):
 #   Column            Non-Null Count  Dtype 
---  ------            --------------  ----- 
 0   Unnamed: 0        235 non-null    int64 
 1   nama_file         235 non-null    object
 2   Nomor Putusan     235 non-null    object
 3   Nama Terdakwa 1   235 non-null    object
 4   Nama Terdakwa 2   36 non-null     object
 5   Nama Terdakwa 3   8 non-null      object
 6   Tuntutan Pidana   235 non-null    object
 7   Tuntutan KUHP     235 non-null    object
 8   Tuntutan Hukuman  235 non-null    object
 9   Putusan Pidana    235 non-null    object
 10  Putusan Hukuman   235 non-null    object
 11  Tanggal Putusan   234 non-null    object
 12  Hakim Ketua       235 non-null    object
 13  Hakim Anggota 1   227 non-null    object
 14  Hakim Anggota 2   152 non-null    object
 15  Panitera          235 non-null    object
 16  Penuntut Umum     235 non-null    object
 17  content         

In [8]:
text_columns = main_df.select_dtypes(include='object').columns

In [9]:
text_columns

Index(['nama_file', 'Nomor Putusan', 'Nama Terdakwa 1', 'Nama Terdakwa 2',
       'Nama Terdakwa 3', 'Tuntutan Pidana', 'Tuntutan KUHP',
       'Tuntutan Hukuman', 'Putusan Pidana', 'Putusan Hukuman',
       'Tanggal Putusan', 'Hakim Ketua', 'Hakim Anggota 1', 'Hakim Anggota 2',
       'Panitera', 'Penuntut Umum', 'content'],
      dtype='object')

---


In [10]:
def normalize_text(text):
    # text = re.sub(r'\bmajelis\b', '', text, flags=re.I)
    # text = re.sub(r'\s+', ' ', text)
    # text = re.sub(r'\s+/', '/', text) 
    text = re.sub(r'^\s*,', '', text)
    # text = re.sub(r'["“”]', '', text)
    # text = re.sub(r'[":”]', '', text) 
    return text.strip()

In [11]:
def generate_label(entities):
    label = {}

    
    def update_label(entity_list, label, label_value):
        if isinstance(entity_list, list) and entity_list: 
            if len(entity_list) > 1:
                for ent in entity_list:
                    # Normalisasi entitas sebelum ditambahkan ke label
                    normalized_ent = normalize_text(ent)
                    if normalized_ent:
                        label[label_value] = label.get(label_value, []) + [normalized_ent] 
            else:
                # Jika hanya ada satu entitas, normalisasi terlebih dahulu
                normalized_ent = normalize_text(entity_list[0])
                label[label_value] = label.get(label_value, []) + [normalized_ent]
        elif isinstance(entity_list, str) and entity_list.strip():
            # Normalisasi entitas yang berupa string
            normalized_ent = normalize_text(entity_list)
            label[label_value] = label.get(label_value, []) + [normalized_ent]
            
    

    # Melabeli entitas yang ada di 'Penuntut Umum', 'Nama Terdakwa', dll.
    if 'Penuntut Umum' in entities and entities['Penuntut Umum']:
        update_label(entities['Penuntut Umum'], label, "B_PROS")

    for i in range(1, 4): 
        key = f'Nama Terdakwa {i}'
        if key in entities and entities[key]:
            update_label(entities[key], label, "B_DEFN")

    for i in range(1, 3):
        key = f'Hakim Anggota {i}'
        if key in entities and entities[key]:
            update_label(entities[key], label, "B_JUDG")

    if 'Tuntutan Hukuman' in entities and entities['Tuntutan Hukuman']:
        value = entities['Tuntutan Hukuman'].strip()
        if value in label:
            label["B_PENA"] = label.get("B_PENA", []) + [value]
        else:
            update_label(entities['Tuntutan Hukuman'], label, "B_PENA")
        
    if 'Putusan Hukuman' in entities and entities['Putusan Hukuman']:
        value = entities['Putusan Hukuman'].strip()
        if value in label:
            label["B_PUNI"] = label.get("B_PUNI", []) + [value]
        else:
            update_label(entities['Putusan Hukuman'], label, "B_PUNI")   

    if 'Nomor Putusan' in entities:
        update_label(entities['Nomor Putusan'], label, "B_VERN")
    if 'Tanggal Putusan' in entities:
        update_label(entities['Tanggal Putusan'], label, "B_TIMV")
    if 'Hakim Ketua' in entities:
        update_label(entities['Hakim Ketua'], label, "B_JUDP")
    if 'Panitera' in entities:
        update_label(entities['Panitera'], label, "B_REGI")
    if 'Tuntutan Pidana' in entities:
        update_label(entities['Tuntutan Pidana'], label, "B_CRIA")
    if 'Tuntutan KUHP' in entities:
        update_label(entities['Tuntutan KUHP'], label, "B_ARTV")
        
    return label


In [12]:
# label = generate_label(main_df.iloc[3].to_dict())
# label


In [13]:
    
def labeling_token(text, label_dict):
    text = text.lower()  # Tokenize the text
    tokens = text.split()
    # print(tokens)# Tokenize the text using whitespace  
    labeled_tokens = ['O'] * len(tokens) 
    find_label = dict()
    for label, entities in label_dict.items():
            if isinstance(entities, list): 
                for entity in entities:
                    words = entity.split()
                    if not words:  # Skip if words is empty
                        continue
                    current_dict = find_label
                    for word in words[:-1]:
                        word = re.sub(r'[.,;":]', '', word)
                        current_dict = current_dict.setdefault(word, {})
                    last_word = re.sub(r'[.,;":]', '', words[-1]) 
                    current_dict[last_word] = {'label': label}
            else:  
                words = entities.split()
                if not words:  # Skip if words is empty
                    continue
                current_dict = find_label
                for word in words[:-1]:
                    word = re.sub(r'[.,;":]', '', word)  
                    current_dict = current_dict.setdefault(word, {})
                last_word = re.sub(r'[.,;":]', '', words[-1])
                current_dict[last_word] = {'label': label}

    temp_idx_token = []  
    find_label_selected = find_label

    for i, token in enumerate(tokens):
        clean_token = re.sub(r'[.,;":]', '', token)
        if clean_token in find_label_selected:
            find_label_selected = find_label_selected[clean_token]
            temp_idx_token.append(i)
            if 'label' in find_label_selected:
                tag = find_label_selected['label']
                for ind in range(len(temp_idx_token)):
                    if ind == 0:
                        labeled_tokens[temp_idx_token[ind]] = tag
                    else:
                        labeled_tokens[temp_idx_token[ind]] = tag.replace('B', 'I')
                temp_idx_token = [] 
                find_label_selected = find_label 
        else:
            temp_idx_token = []
            find_label_selected = find_label 

    return labeled_tokens


In [14]:
main_df['content'][6]

'PUTUSAN\n Nomor 392/Pid. B/2019/PN Bkl DEMI KEADILAN BERDASARKAN KETUHANAN YANG MAHA ESA Pengadilan Negeri Bangkalan yang mengadili perkara pidana dengan acara pemeriksaan biasa dalam tingkat pertama menjatuhkan putusan sebagai berikut dalam perkara Terdakwa :\n\nNama lengkap : Heru Irawan Bin Mustar ;. \n\nTempat lahir : Bangkalan ;. \n\nUmur/Tanggal lahir : 25/10 Desember 1994 ;\nJenis kelamin : Laki-laki ;. \n\nKebangsaan : Indonesia ;. \n\nTempat tinggal : Dsn.  Galis Ds.  Sendang Laok Kec.  Labang Kab.  Bangkalan. \n\nAgama : Islam ;. \n\nPekerjaan : tidak bekerja ;\nTerdakwa Heru Irawan Bin Mustar ditahan dalam dalam perkara lain ;\nTerdakwa dipersidangan didampingi oleh Penasehat Hukum yang ditunjuk Pengadilan Negeri Bangkalan tanggal 07 Nopember 2019, Nomor 392/Pen. Pid. B/2019/PN. Bkl.  ;\nPengadilan Negeri tersebut;\nSetelah membaca :  -Penetapan Ketua Pengadilan Negeri Bangkalan Nomor 392/Pid. B/2019/PN Bkl tanggal 29 Oktober 2019 tentang penunjukan Majelis Hakim;\n-Penetap

In [15]:
testlabel = generate_label(main_df.iloc[6].to_dict())
testlabel

{'B_PROS': ['fajrini faisah, s. h. .,'],
 'B_DEFN': ['heru irawan bin mustar'],
 'B_PENA': ['3 (tiga) tahun , dikurangi selama terdakwa ditahan dalam tahanan'],
 'B_PUNI': ['2 (dua) tahun'],
 'B_VERN': ['392/pid. b/2019/pn bkl'],
 'B_TIMV': ['tanggal 23 desember 2019'],
 'B_JUDP': ['muhamad baginda rajoko harahap, s. h. , m. h. ,'],
 'B_REGI': ['hairus salam, sh. ,'],
 'B_CRIA': ['pencurian yang didahului, disertai atau diikuti dengan kekerasan atau ancaman kekerasan, terhadap orang dengan maksud untuk emmpersiap atau mempermudah pencurian, atau dalam hal tertangkap tangan , untuk memungkinkan melarikan diri sendiri atau peserta lainnya, aytau untuk tetap meguasai barang yang dicurinya, jika  dengan bersekutu "'],
 'B_ARTV': ['pasal pasal 365 ayat (2) ke-1 dan ke-2 kuhp']}

In [16]:
testlabelstokens = labeling_token(main_df.iloc[6]['content'], testlabel)
# labelstokens[:20]

In [17]:
testlabelstokens[:2000]

['O',
 'O',
 'B_VERN',
 'I_VERN',
 'I_VERN',
 'O',
 'O',
 'O',
 'O',
 'O',
 'O',
 'O',
 'O',
 'O',
 'O',
 'O',
 'O',
 'O',
 'O',
 'O',
 'O',
 'O',
 'O',
 'O',
 'O',
 'O',
 'O',
 'O',
 'O',
 'O',
 'O',
 'O',
 'O',
 'O',
 'O',
 'O',
 'O',
 'B_DEFN',
 'I_DEFN',
 'I_DEFN',
 'I_DEFN',
 'O',
 'O',
 'O',
 'O',
 'O',
 'O',
 'O',
 'O',
 'O',
 'O',
 'O',
 'O',
 'O',
 'O',
 'O',
 'O',
 'O',
 'O',
 'O',
 'O',
 'O',
 'O',
 'O',
 'O',
 'O',
 'O',
 'O',
 'O',
 'O',
 'O',
 'O',
 'O',
 'O',
 'O',
 'O',
 'O',
 'O',
 'O',
 'O',
 'O',
 'O',
 'O',
 'O',
 'O',
 'B_DEFN',
 'I_DEFN',
 'I_DEFN',
 'I_DEFN',
 'O',
 'O',
 'O',
 'O',
 'O',
 'O',
 'O',
 'O',
 'O',
 'O',
 'O',
 'O',
 'O',
 'O',
 'O',
 'O',
 'O',
 'O',
 'O',
 'O',
 'O',
 'O',
 'O',
 'O',
 'O',
 'O',
 'O',
 'O',
 'O',
 'O',
 'O',
 'O',
 'O',
 'O',
 'O',
 'O',
 'O',
 'O',
 'O',
 'B_VERN',
 'I_VERN',
 'I_VERN',
 'O',
 'O',
 'O',
 'O',
 'O',
 'O',
 'O',
 'O',
 'O',
 'O',
 'O',
 'O',
 'B_VERN',
 'I_VERN',
 'I_VERN',
 'O',
 'O',
 'O',
 'O',
 'O',
 'O',
 'O

In [18]:
def handleDuplicatePena(sequences):
    countPena = 0

    for sequence in sequences:
        for i, label in enumerate(sequence):
            if label == 'B_PENA': 
                countPena += 1
                if countPena > 1:  
                    sequence[i] = 'B_PUNI' 
            elif label == 'I_PENA':  
                if countPena > 1: 
                    sequence[i] = 'I_PUNI' 

    return sequences


In [19]:
def countLabel(doc_idx, data, label_ori):
    result = {}
    label_found = set()
    label_list = set(['B_ARTV', 'B_DEFN', 'B_PROS', 'B_CRIA', 'B_JUDP', 'B_VERN', 'B_PUNI', 'B_JUDG', 'B_REGI', 'B_TIMV', 'B_PENA'])
    for i, row in data.iterrows():
      for t, l in zip(row["word"], row["tag"]):
        if l != 'O' and l.replace('I_', 'B_') not in label_found:
          label_found.add(l.replace('I_', 'B_'))

    label_missing = label_list - label_found
    result[f"Dokumen Ke-{doc_idx}"] = (len(label_found), len(label_ori), label_missing)
    return result



def anotasi(data):
    content_results = pd.DataFrame(columns=["doc", "word", "tag"])
    count_label = {}
    labels = []

    for doc_idx, (_, row) in tqdm(enumerate(data.iterrows()), total=len(data), desc="Annotating"):
        temp_results = {"doc": [], "word": [], "tag": []}

        label = generate_label(row)
        labels.append(label)
        content = row["content"]
        labeled_tokens = labeling_token(content, label)

        doc_str = f"doc:{doc_idx+1}"
        temp_results["doc"].append(doc_str)
        temp_results["word"].append(content.split())
        temp_results["tag"].append(labeled_tokens)
        temp_results['tag'] = handleDuplicatePena(temp_results['tag'])

        temp_data = pd.DataFrame(temp_results)
        count_label.update(countLabel(f"{doc_idx}", temp_data, label))
        content_results = pd.concat([content_results, temp_data], ignore_index=True)

    return content_results, count_label, labels


In [20]:


def accuracy(result):
  sum_label = 0
  label_in = 0
  for key, value in result.items():
    print(f"{key} => Data Terlebel : {value[0]} ; Total Label : {value[1]} ; Label Hilang : {value[2]}")
    sum_label+= value[1]
    label_in += value[0]

  return f"Accuracy : {label_in/sum_label * 100}"

In [21]:
anot_df, count_label, labels = anotasi(main_df)


Annotating: 100%|██████████| 235/235 [00:01<00:00, 150.79it/s]


In [22]:
anot_df

doc                                               word  \
0      doc:1  [PUTUSAN, Nomor, 192/Pid., B/2019/PN, Bkl, DEM...   
1      doc:2  [PUTUSAN, Nomor, 9/Pid., B/2019/PN, Bkl, DEMI,...   
2      doc:3  [PUTUSAN, Nomor, 108/Pid., B/2020/PN, Bkl, DEM...   
3      doc:4  [PUTUSAN, NOMOR, :, 294/Pid., B/2018/PN., BKL....   
4      doc:5  [PUTUSAN, Nomor, 431/Pid., B/2018/PN, Bkl, DEM...   
..       ...                                                ...   
230  doc:231  [PUTUSAN, Nomor, 31/Pid., B/2025/PN, Bkl, DEMI...   
231  doc:232  [PUTUSAN, Nomor, 47/Pid., B/2025/PN, Bkl, DEMI...   
232  doc:233  [PUTUSAN, Nomor, 76/Pid., B/2025/PN, Bkl, DEMI...   
233  doc:234  [PUTUSAN, Nomor, 77/Pid., B/2025/PN, Bkl, DEMI...   
234  doc:235  [Nomor, 60/Pid., B/2025/PN, Bkl, DEMI, KEADILA...   

                                                   tag  
0    [O, O, B_VERN, I_VERN, I_VERN, O, O, O, O, O, ...  
1    [O, O, B_VERN, I_VERN, I_VERN, O, O, O, O, O, ...  
2    [O, O, B_VERN, I_VERN, I_VERN, O, O, O, O, O, ...  
3    [O, O, O, B_VERN, I_VERN, I_VERN, O, O, O, O, ...  
4    [O, O, O, O, O, O, O, O, O, O, O, O, O, O, O, ...  
..                                                 ...  
230  [O, O, B_VERN, I_VERN, I_VERN, O, O, O, O, O, ...  
231  [O, O, B_VERN, I_VERN, I_VERN, O, O, O, O, O, ...  
232  [O, O, O, O, O, O, O, O, O, O, O, O, O, O, O, ...  
233  [O, O, B_VERN, I_VERN, I_VERN, O, O, O, O, O, ...  
234  [O, B_VERN, I_VERN, I_VERN, O, O, O, O, O, O, ...  

[235 rows x 3 columns]

In [23]:
accuracy(count_label)

Dokumen Ke-0 => Data Terlebel : 11 ; Total Label : 11 ; Label Hilang : set()
Dokumen Ke-1 => Data Terlebel : 11 ; Total Label : 11 ; Label Hilang : set()
Dokumen Ke-2 => Data Terlebel : 11 ; Total Label : 11 ; Label Hilang : set()
Dokumen Ke-3 => Data Terlebel : 11 ; Total Label : 11 ; Label Hilang : set()
Dokumen Ke-4 => Data Terlebel : 10 ; Total Label : 11 ; Label Hilang : {'B_PENA'}
Dokumen Ke-5 => Data Terlebel : 10 ; Total Label : 11 ; Label Hilang : {'B_VERN'}
Dokumen Ke-6 => Data Terlebel : 10 ; Total Label : 10 ; Label Hilang : {'B_JUDG'}
Dokumen Ke-7 => Data Terlebel : 10 ; Total Label : 11 ; Label Hilang : {'B_JUDG'}
Dokumen Ke-8 => Data Terlebel : 10 ; Total Label : 11 ; Label Hilang : {'B_JUDG'}
Dokumen Ke-9 => Data Terlebel : 10 ; Total Label : 11 ; Label Hilang : {'B_PENA'}
Dokumen Ke-10 => Data Terlebel : 10 ; Total Label : 11 ; Label Hilang : {'B_PENA'}
Dokumen Ke-11 => Data Terlebel : 11 ; Total Label : 11 ; Label Hilang : set()
Dokumen Ke-12 => Data Terlebel : 11 ; T

'Accuracy : 93.01242236024845'

In [25]:
import csv
import os
import pandas as pd

# Create output directory if it doesn't exist
output_dir = os.path.join(os.getcwd(), 'OUPUT')
os.makedirs(output_dir, exist_ok=True)

# Path for the output CSV file
output_file = os.path.join('../../Datasets/FINAL/DATASET_BERT_SENTENCE.csv')

# Open file for writing
with open(output_file, 'w', newline='', encoding='utf-8') as f:
    writer = csv.writer(f)
    writer.writerow(('text', 'labels'))
    
    # Process each document
    for _, row in anot_df.iterrows():
        # Get words and tags from the row
        doc_id = row['doc']
        words = row['word']
        tags = row['tag']
        
        # Skip empty entries
        if not isinstance(words, list) or not words:
            continue
            
        # Convert lists to space-separated strings
        text_sentence = ' '.join(words)
        tags_sentence = ' '.join(tags)
        
        # Write to CSV
        writer.writerow([text_sentence, tags_sentence])
        
        # Print sample for verification
        if _ < 3:  # Only print first 3 for clarity
            print(f"Document: {doc_id}")
            print(f"Text: {text_sentence[:100]}...")
            print(f"Tags: {tags_sentence[:100]}...")
            print("-" * 80)

print(f"\nConversion completed. Output saved to {output_file}")

# Read back the created file to show a sample
try:
    bert_data = pd.read_csv(output_file)
    print(f"\nCreated dataset has {len(bert_data)} rows")
    print("\nSample of the created dataset:")
    display(bert_data.head(3))
except Exception as e:
    print(f"Error reading the created file: {e}")

Document: doc:1
Text: PUTUSAN Nomor 192/Pid. B/2019/PN Bkl DEMI KEADILAN BERDASARKAN KETUHANAN YANG MAHA ESA Pengadilan Ne...
Tags: O O B_VERN I_VERN I_VERN O O O O O O O O O O O O O O O O O O O O O O O O O O O O O O O B_DEFN I_DEFN...
--------------------------------------------------------------------------------
Document: doc:2
Text: PUTUSAN Nomor 9/Pid. B/2019/PN Bkl DEMI KEADILAN BERDASARKAN KETUHANAN YANG MAHA ESA Pengadilan Nege...
Tags: O O B_VERN I_VERN I_VERN O O O O O O O O O O O O O O O O O O O O O O O O O O O O O O O O B_DEFN I_DE...
--------------------------------------------------------------------------------
Document: doc:3
Text: PUTUSAN Nomor 108/Pid. B/2020/PN Bkl DEMI KEADILAN BERDASARKAN KETUHANAN YANG MAHA ESA Pengadilan Ne...
Tags: O O B_VERN I_VERN I_VERN O O O O O O O O O O O O O O O O O O O O O O O O O O O O O O O O O O O B_DEF...
--------------------------------------------------------------------------------

Conversion completed. Output saved to ../../Data

text  \
0  PUTUSAN Nomor 192/Pid. B/2019/PN Bkl DEMI KEAD...   
1  PUTUSAN Nomor 9/Pid. B/2019/PN Bkl DEMI KEADIL...   
2  PUTUSAN Nomor 108/Pid. B/2020/PN Bkl DEMI KEAD...   

                                              labels  
0  O O B_VERN I_VERN I_VERN O O O O O O O O O O O...  
1  O O B_VERN I_VERN I_VERN O O O O O O O O O O O...  
2  O O B_VERN I_VERN I_VERN O O O O O O O O O O O...

## Saving in BIO Format (One token per line)

In [ ]:
# # Save in standard BIO format (one token per line with empty lines between sentences)
# bio_file_path = os.path('../../Datasets/FINAL/DATASET_BIO.txt')

# with open(bio_file_path, 'w', encoding='utf-8') as f:
#     # Add document separator for the first document
#     f.write('# doc:1\n')
    
#     current_doc = 'doc:1'
    
#     for _, row in anot_df.iterrows():
#         doc_id = row['doc']
#         words = row['word']
#         tags = row['tag']
        
#         # Skip empty entries
#         if not isinstance(words, list) or not words:
#             continue
        
#         # Add document separator if we're at a new document
#         if doc_id != current_doc:
#             f.write(f'\n# {doc_id}\n')
#             current_doc = doc_id
        
#         # Write each token and its tag on a separate line
#         for word, tag in zip(words, tags):
#             f.write(f'{word}\t{tag}\n')
        
#         # Add an empty line between sentences within the same document
#         f.write('\n')

# print(f"\nBIO format data saved to {bio_file_path}")

# # Show a sample of the BIO file
# with open(bio_file_path, 'r', encoding='utf-8') as f:
#     sample_lines = [line.strip() for line in f.readlines()[:20]]
#     print("\nSample of the BIO format file (first 20 lines):")
#     for line in sample_lines:
#         print(line)

## Analyze Entity Distribution

In [ ]:
# import matplotlib.pyplot as plt
# import seaborn as sns

# # Count entity occurrences
# entity_counts = {}
# for _, row in anot_df.iterrows():
#     tags = row['tag']
#     if not isinstance(tags, list):
#         continue
        
#     for tag in tags:
#         if tag != 'O':
#             # Extract base entity type (B_XXX or I_XXX → XXX)
#             entity_type = tag[2:] if tag.startswith('B_') or tag.startswith('I_') else tag
#             entity_counts[entity_type] = entity_counts.get(entity_type, 0) + 1

# # Sort by count
# sorted_entities = sorted(entity_counts.items(), key=lambda x: x[1], reverse=True)
# entities = [e[0] for e in sorted_entities]
# counts = [e[1] for e in sorted_entities]

# # Plot
# plt.figure(figsize=(12, 6))
# sns.barplot(x=entities, y=counts)
# plt.title('Entity Type Distribution')
# plt.xlabel('Entity Type')
# plt.ylabel('Count')
# plt.xticks(rotation=45)
# plt.tight_layout()
# plt.show()

# print("Entity counts:")
# for entity, count in sorted_entities:
#     print(f"{entity}: {count}")

## Create Files for Hugging Face Transformers

In [ ]:
# # Create train/validation/test splits
# from sklearn.model_selection import train_test_split

# # Convert to a format suitable for splitting
# dataset_rows = []
# for _, row in anot_df.iterrows():
#     doc_id = row['doc']
#     words = row['word']
#     tags = row['tag']
    
#     if not isinstance(words, list) or not words:
#         continue
        
#     dataset_rows.append({
#         'doc_id': doc_id,
#         'words': words,
#         'tags': tags
#     })

# # Create splits
# train_data, temp_data = train_test_split(dataset_rows, test_size=0.3, random_state=42)
# val_data, test_data = train_test_split(temp_data, test_size=0.5, random_state=42)

# print(f"Train set: {len(train_data)} documents")
# print(f"Validation set: {len(val_data)} documents")
# print(f"Test set: {len(test_data)} documents")

# # Function to write data in the CoNLL-2003 format
# def write_conll_file(filename, data):
#     with open(filename, 'w', encoding='utf-8') as f:
#         for item in data:
#             words = item['words']
#             tags = item['tags']
            
#             for word, tag in zip(words, tags):
#                 f.write(f"{word} {tag}\n")
#             f.write("\n")  # Empty line between documents

# # Write files
# data_dir = os.path.join(output_dir, 'huggingface_data')
# os.makedirs(data_dir, exist_ok=True)

# train_file = os.path.join(data_dir, 'train.txt')
# val_file = os.path.join(data_dir, 'dev.txt')
# test_file = os.path.join(data_dir, 'test.txt')

# write_conll_file(train_file, train_data)
# write_conll_file(val_file, val_data)
# write_conll_file(test_file, test_data)

# print(f"\nFiles created in {data_dir} directory:")
# print(f"- Train file: {train_file}")
# print(f"- Validation file: {val_file}")
# print(f"- Test file: {test_file}")

# # Sample from train file
# with open(train_file, 'r', encoding='utf-8') as f:
#     sample_lines = [line.strip() for line in f.readlines()[:10]]
#     print("\nSample from train file:")
#     for line in sample_lines:
#         print(line)

## How to Use the Converted Data with BERT

The data has been converted into several formats:

1. **Sentence-based CSV**: Each row contains a complete sentence and its tags
2. **BIO format**: Standard token-per-line format with empty lines between sentences
3. **Hugging Face splits**: Train/validation/test files ready for fine-tuning

These formats are compatible with different NER approaches:

- The sentence-based CSV works well with simple BERT models that process whole sentences
- The BIO format is suitable for most NER libraries and frameworks
- The Hugging Face splits can be directly used with the Transformers library

Next, you can use this data to train your multilingual BERT model with MLP as planned in your main notebook.